In [1]:
!pip install simpletransformers
!python3 -m spacy download fr_core_news_md

     |████████████████████████████████| 231 kB 5.2 MB/s 
     |████████████████████████████████| 8.3 MB 43.1 MB/s 
     |████████████████████████████████| 2.9 MB 35.8 MB/s 
     |████████████████████████████████| 3.3 MB 32.8 MB/s 
     |████████████████████████████████| 1.2 MB 39.5 MB/s 
     |████████████████████████████████| 1.7 MB 35.4 MB/s 
     |████████████████████████████████| 290 kB 45.2 MB/s 
     |████████████████████████████████| 43 kB 1.9 MB/s 
     |████████████████████████████████| 895 kB 39.5 MB/s 
     |████████████████████████████████| 56 kB 4.3 MB/s 
     |████████████████████████████████| 596 kB 43.7 MB/s 
     |████████████████████████████████| 97 kB 6.5 MB/s 
     |████████████████████████████████| 180 kB 46.7 MB/s 
     |████████████████████████████████| 139 kB 48.9 MB/s 
     |████████████████████████████████| 63 kB 1.8 MB/s 
     |████████████████████████████████| 125 kB 50.0 MB/s 
     |████████████████████████████████| 1.3 MB 31.4 MB/s 
     |█████████████████

     |████████████████████████████████| 88.6 MB 1.3 MB/s 
  Created wheel for fr-core-news-md: filename=fr_core_news_md-2.2.5-py3-none-any.whl size=90338488 sha256=8787fdf365d29cf2fd084d6756b6e424e8aa2485cca3c13ab16adbb7958522eb
  Stored in directory: /tmp/pip-ephem-wheel-cache-ar7uay4a/wheels/2e/26/ff/ce93eb966e7176ebe81e6c98209582e13e108cdd2d6d636df0
Successfully built fr-core-news-md
✔ Download and installation successful
You can now load the model via spacy.load('fr_core_news_md')


In [ ]:
from google.colab import drive
drive.mount("/content/drive", force_remount=True)
chemin = "/content/drive/MyDrive/Stage Defense"


Mounted at /content/drive


In [ ]:
import re

from bs4 import BeautifulSoup
import pandas as pd
import numpy as np


import spacy

from sklearn.model_selection import train_test_split, KFold, StratifiedKFold
from sklearn.metrics import classification_report
from simpletransformers.ner import NERModel, NERArgs


2021-08-05 17:34:41.347881: I tensorflow/stream_executor/platform/default/dso_loader.cc:53] Successfully opened dynamic library libcudart.so.11.0


In [ ]:
nlp = spacy.load('fr_core_news_md')

#Chargement Corpus

In [ ]:
def from_xml_to_df(fichierxml,limitedebut=None,limitefin=None,skip=[], documentlevel=False, selecteur="mention,meronyme"):
    'Extrait les phrases du fichier xml balisé et retourne un dataframe contenant les token au format BIO'
    if limitedebut and limitefin:
      assert limitedebut <= limitefin
    dico = {"mention":"Mention_La_Defense","meronyme":"Mention_Meronyme_La_Defense"}
    soup = BeautifulSoup(open(fichierxml,encoding="utf8"), 'lxml')
    data = []
    i=0
    for texte in soup.select("article > texte,titre"):
        ident = int(texte.parent.get('id')) #id de l'article
        if (limitedebut and ident < limitedebut) or (ident in skip): continue
        if limitefin and ident > limitefin: break
        
        ls_mentions = []
        for mention in texte.select(selecteur):
            ls_mentions.append((mention.text, dico[mention.name]))
            mention.string = "ENTITE_MENTION_La_Defense"
        
        doc = nlp(texte.text, disable=[ 'tagger', 'ner'])
        for sent in doc.sents:
            for token in sent:
                if token.is_space:continue
                if token.text == "ENTITE_MENTION_La_Defense":
                    tuple_cat_mention = ls_mentions.pop(0)
                    doc2 = nlp(tuple_cat_mention[0], disable=['parser', 'tagger', 'ner'])
                    l = 0
                    for token2 in doc2:
                        if l>=1:
                          BIO = "I-"
                        else:
                          BIO = "B-"
                            
                        data.append([i, token2.text, BIO+tuple_cat_mention[1]])
                        l+=1
                else:
                    data.append([i, token.text, "O"])
            if not documentlevel:
                i+=1
        if documentlevel:
            i+=1
            
    df = pd.DataFrame(data,columns=["sentence_id","words","labels"])
    
    return df

In [ ]:
def train_test_split_tokens(df, taille_train):
  '''coupe la dataframe en deux dataframes selon une portion indiquée'''
  phrases = df.sentence_id.unique()
  phrases_train, phrases_test = train_test_split(phrases,train_size=taille_train)
  df_train = df[df.sentence_id.isin(phrases_train)]
  df_test = df[df.sentence_id.isin(phrases_test)]
  return df_train,df_test

In [ ]:
fichierxml = chemin + "/Corpus/Presse/grandfinal_annoté_manu.xml"
df_corpus =from_xml_to_df(fichierxml,limitedebut=0,limitefin=352,documentlevel=False)
df_corpus.to_csv(chemin+"/tokens_entites_mentions.csv",sep='\t',index=False)

In [ ]:
df_corpus = pd.read_csv(chemin+"/tokens_entites_mentions.csv",sep="\t")

In [ ]:
df_train, df_test = train_test_split_tokens(df_corpus,0.8)

In [ ]:
df_test

sentence_id      words labels
127               5          -      O
128               5      Arche      O
129               5          (      O
130               5    Epadesa      O
131               5          )      O
...             ...        ...    ...
217108        11143  inférieur      O
217109        11143          à      O
217110        11143        0,1      O
217111        11143          %      O
217112        11143          .      O

[43290 rows x 3 columns]

#Entraînement

In [ ]:
from sklearn.utils.class_weight import compute_class_weight

On prépare le modèle. On lui indique les etiquettes possibles.
25 époques.
Besoin d'utiliser un bon GPU (comme ceux de Google) sinon c'est beaucoup trop long

In [ ]:
custom_labels = ["O","B-Mention_La_Defense","B-Mention_Meronyme_La_Defense","I-Mention_La_Defense","I-Mention_Meronyme_La_Defense"]

model_args = NERArgs()
model_args.labels_list = custom_labels
model_args.num_train_epochs = 20
model_args.learning_rate = 4e-5
model_args.overwrite_output_dir = True
model_args.train_batch_size = 16
#model_args.evaluate_during_training = True
#model_args.use_early_stopping = True


In [ ]:
len(df_corpus.index)

217148

On Garde uniquement les phrases qui possèdent des mentions pour équilibrer un peu les classes (et ne pas avoir trop de tokens O)

In [ ]:
df_corpus= df_corpus[df_corpus.sentence_id.isin(df_corpus.sentence_id[df_corpus.labels != "O"])]

In [ ]:
len(df_corpus.index)

5854

In [ ]:
def validation_croisee(df,model_args,plis=2):
  
  df = df[df.sentence_id.isin(df.sentence_id[df.labels != "O"])]
  X1 = df.sentence_id.to_numpy()
  X2 = df.words.to_numpy()
  y = df.labels.to_numpy()
  X = []
  y_true,y_pred = [], []
  phrases = df.sentence_id.unique()
  #phrases_train, phrases_test = train_test_split(phrases,train_size=taille_train)
  kf = KFold(n_splits=plis, random_state=None)
  scores = []
  for train_index, test_index in kf.split(phrases):
    phrases_train = phrases[train_index]
    phrases_test = phrases[test_index]
    df_train = df[df.sentence_id.isin(phrases_train)]
    print("chargement et entraînement")
    weights =  compute_class_weight('balanced',custom_labels,df_train.labels).tolist()
    model = NERModel("camembert","camembert-base",args=model_args,labels=custom_labels,weight=weights)
    #df_train = pd.DataFrame(np.stack((X1_train,X2,train,y_train), columns=["sentence_id","words","labels"]))
    #df_test = pd.DataFrame(np.stack((X1_test,X2,test,y_test), columns=["sentence_id","words","labels"]))
    df_test = df[df.sentence_id.isin(phrases_test)]
    print(df_test)
    y_test = df_test.labels.tolist()

    model.train_model(df_train,
                  output_dir=chemin+"/Modeles/Modele_Camembert_1")
    to_predict= []
    for phrase in phrases_test:
      words = df_test[df_test.sentence_id == phrase].words.tolist()
      to_predict.append(words)
    #print("WA", len())
    words_to_pred = [w for u in to_predict for w in u]
    preds_list,ouputs = model.predict(to_predict, split_on_space=False)
    print("to_predict",to_predict)
    print("preds_list",preds_list)
    X.extend(words_to_pred)
    y_true.extend(y_test)
    #preds = preds_list
    preds =[(dic[word],word) for phrase in preds_list for dic in phrase for word,label in dic.items()]
    print(preds)
    assert len(words_to_pred)==len(y_test)
    for i in range(len(y_test) - 1):
      if len(y_test)>len(preds):
         if words_to_pred[i] != preds[i][1] and words_to_pred[i+1] == preds[i][1]:
          print("DIFFERENT",i, words_to_pred[i], preds[i])
          print(words_to_pred[i+1],preds[i][1] )
          preds.insert(i,("O","."))
          
          #break
      else:
        break
    preds = [pred[0] for pred in preds]
    print(len(df_test.index), len(df_test.words),len(y_test),len(preds))

    y_pred.extend(preds)
    
  return model,X, y_true,y_pred


    
    

    

In [ ]:
last_model,X, y_true, y_pred = validation_croisee(df_corpus,model_args,plis=4)

chargement et entraînement


Downloading:   0%|          | 0.00/508 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/445M [00:00<?, ?B/s]

Some weights of the model checkpoint at camembert-base were not used when initializing CamembertForTokenClassification: ['lm_head.layer_norm.bias', 'lm_head.layer_norm.weight', 'lm_head.bias', 'lm_head.decoder.weight', 'lm_head.dense.bias', 'lm_head.dense.weight']
- This IS expected if you are initializing CamembertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing CamembertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of CamembertForTokenClassification were not initialized from the model checkpoint at camembert-base and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream tas

Downloading:   0%|          | 0.00/811k [00:00<?, ?B/s]

...

Running Epoch 23 of 25:   0%|          | 0/18 [00:00<?, ?it/s]

Running Epoch 24 of 25:   0%|          | 0/18 [00:00<?, ?it/s]

  0%|          | 0/47 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/6 [00:00<?, ?it/s]

to_predict [['Ce', 'fonds', "d'", 'investissement', 'a', "d'", 'autant', 'moins', 'cassé', 'sa', 'tirelire', "qu'", 'il', 'y', 'a', 'un', 'an', 'et', 'demi', ',', 'la', 'Défense', 'était', 'en', 'bas', 'de', 'cycle', ',', 'poursuit', 'Caroline', 'Dheilly', '.'], ['Il', 'y', 'avait', 'beaucoup', 'de', 'bureaux', 'vacants', ',', 'des', 'tours', 'fraîchement', 'livrées', 'sans', 'locataires', ',', 'des', 'interrogations', 'sur', 'les', 'niveaux', 'de', 'loyers', '...', '»', 'Depuis', ',', "l'", 'horizon', 'la', 'Défense', "s'", 'est', 'un', 'peu', 'dégagé', ':', 'le', 'taux', 'de', 'vacance', 'des', 'bureaux', ',', 'qui', 'frisait', 'les', '14', '%', 'début', '2014', ',', 'est', 'redescendu', 'à', '11', '%', '.'], ['Quelques', 'transactions', 'ont', 'illustré', 'ce', 'regain', 'de', 'forme', 'pour', 'Coeur', 'Défense', ',', 'un', 'énorme', 'ensemble', 'immobilier', 'de', '160', '000', 'm2', '.'], ['Début', '2015', ',', 'Thales', 'a', 'quitté', 'Neuilly', 'pour', "s'", 'installer', 'dans',

In [ ]:
len(y_pred), len(y_true)

(5854, 5854)

#Tests

In [ ]:
predictions, raw_outputs = last_model.predict(["J'irais manger au restaurant demain.",
                                               "Je cherche un diamant pour ma soeur",
                                               "On se rejoint à la Défense du coup",
                                               "Tu fais quoi dans le quartier?",
                                               "J'irais au centre commercial dans l'apres-midi",
                                               "Nous avons pu manger à l'oeil sur l'esplanade ; Les pigeons nous regardaient.",
                                               "C'est pourquoi de plus en plus d'investisseurs s'intéressent au plus grand Centre Commercial d'Europe."])
for pred,raw in zip(predictions,raw_outputs):
  print(pred)

  0%|          | 0/7 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

[{"J'irais": 'O'}, {'manger': 'O'}, {'au': 'O'}, {'restaurant': 'O'}, {'demain.': 'O'}]
[{'Je': 'O'}, {'cherche': 'O'}, {'un': 'O'}, {'diamant': 'O'}, {'pour': 'O'}, {'ma': 'O'}, {'soeur': 'O'}]
[{'On': 'O'}, {'se': 'O'}, {'rejoint': 'O'}, {'à': 'O'}, {'la': 'B-Mention_La_Defense'}, {'Défense': 'I-Mention_La_Defense'}, {'du': 'O'}, {'coup': 'O'}]
[{'Tu': 'O'}, {'fais': 'O'}, {'quoi': 'O'}, {'dans': 'O'}, {'le': 'B-Mention_La_Defense'}, {'quartier?': 'I-Mention_La_Defense'}]
[{"J'irais": 'O'}, {'au': 'B-Mention_Meronyme_La_Defense'}, {'centre': 'I-Mention_Meronyme_La_Defense'}, {'commercial': 'I-Mention_Meronyme_La_Defense'}, {'dans': 'O'}, {"l'apres-midi": 'O'}]
[{'Nous': 'O'}, {'avons': 'O'}, {'pu': 'O'}, {'manger': 'O'}, {'à': 'O'}, {"l'oeil": 'O'}, {'sur': 'O'}, {"l'esplanade": 'B-Mention_Meronyme_La_Defense'}, {';': 'O'}, {'Les': 'O'}, {'pigeons': 'O'}, {'nous': 'O'}, {'regardaient.': 'O'}]
[{"C'est": 'O'}, {'pourquoi': 'O'}, {'de': 'O'}, {'plus': 'O'}, {'en': 'O'}, {'plus': 'O'}, 

# Evaluation

In [ ]:
import numpy as np
from sklearn.metrics import recall_score, precision_score, confusion_matrix, accuracy_score

## Evaluation sévère

In [ ]:
rappel = recall_score(y_true=y_true, y_pred=y_pred, labels=custom_labels, average=None)
precision = precision_score(y_true=y_true, y_pred=y_pred, labels=custom_labels, average=None)

In [ ]:
df_resultats = pd.DataFrame({"Rappel":rappel,"Précision":precision}, index=custom_labels)

In [ ]:
df_resultats

Rappel  Précision
O                              0.979437   0.965930
B-Mention_La_Defense           0.875912   0.727273
B-Mention_Meronyme_La_Defense  0.595041   0.720000
I-Mention_La_Defense           0.928058   0.900000
I-Mention_Meronyme_La_Defense  0.575949   0.798246

## Evaluation relâchée

In [ ]:
custom_labels_relax = ["Mention_La_Defense","Mention_Meronyme_La_Defense","O"]


In [ ]:
y_true_relax = np.char.lstrip(np.char.lstrip(y_true,"B-"), "I-")
y_pred_relax = np.char.lstrip(np.char.lstrip(y_pred,"B-"), "I-")

In [ ]:
y_true_relax

array(['Mention_La_Defense', 'Mention_La_Defense', 'Mention_La_Defense',
       ..., 'O', 'O', 'O'], dtype='<U29')

In [ ]:
res = classification_report(y_true_relax,y_pred_relax)

In [ ]:
print(res)

                             precision    recall  f1-score   support

         Mention_La_Defense       0.88      0.94      0.91       554
Mention_Meronyme_La_Defense       0.82      0.61      0.70       437
                          O       0.97      0.98      0.97      4863

                   accuracy                           0.95      5854
                  macro avg       0.89      0.84      0.86      5854
               weighted avg       0.95      0.95      0.95      5854



In [ ]:
rappel_relax = recall_score(y_true=y_true_relax, y_pred=y_pred_relax, labels=custom_labels_relax, average=None)
precision_relax = precision_score(y_true=y_true_relax, y_pred=y_pred_relax, labels=custom_labels_relax, average=None)

In [ ]:
df_resultats_relax = pd.DataFrame({"Rappel":rappel_relax,"Précision":precision_relax}, index=custom_labels_relax)

In [ ]:
df_resultats_relax

Rappel  Précision
Mention_La_Defense           0.927798    0.87415
Mention_Meronyme_La_Defense  0.613272    0.80000
O                            0.977997    0.96451

In [ ]:
matrice_brute = confusion_matrix(y_true_relax, y_pred_relax, labels=custom_labels_relax)

In [ ]:
import seaborn as sns
import matplotlib.pyplot as plt

In [ ]:
labels =  ["La_Defense","Meronyme","O"]

In [ ]:
matrice_confusion = pd.DataFrame(matrice_brute,
                                 index=labels,
                                 columns=labels)

NameError: ignored

In [ ]:
from sklearn.metrics import plot_confusion_matrix

In [ ]:
plt.figure(figsize=(9,7))
sns.heatmap(matrice_confusion, annot=True, cmap='Purples', fmt='g')
plt.title(f'Token Classification CamemBERT\n')
plt.ylabel('Vrai')
plt.xlabel('Prédit')
plt.show()

NameError: ignored

<Figure size 648x504 with 0 Axes>

# Etiquettage Automatique

On va maintenant appliquer le modèle sur l'ensemble du corpus pour l'étiquetter automatiquement

In [ ]:
import glob, os

In [ ]:
def reprettify(pretty):
  ''' Rend le xml final un peu plus joli'''
    reg = re.compile("\n {5,}(</?\w+>)\n {5,}")
    return reg.sub("\\1",pretty)

In [ ]:
def Etiquettage_Camembert(fichier_entree_xml, fichier_sortie_xml, model):
  '''prend un fichier xml en entrée et un modèle entraîné puis produit un nouveau fichier xml avec les balises ajoutées'''
  dico = {"mention":"Mention_La_Defense","meronyme":"Mention_Meronyme_La_Defense"}
  dico = {v:k for k,v in dico.items()}
  soup = BeautifulSoup(open(fichierxml,encoding="utf8"), 'lxml')
  
  if type(model)== str:
    fichier_modele = glob.glob(model+"/*")[-1] + "/model_args.json"
    model = NERModel("camembert",fichier_modele)
  for texte in soup.select("article > texte,titre"):
    parent = texte.parent
    tag = texte.name
    ident = int(parent.get("id"))
    print(ident)
    list_sent_token = [[token.text for token in sent] for sent in nlp(texte.text).sents]
    preds_list = model.predict(list_sent_token, split_on_space=False)
    texte_balisé = balise_texte(preds_list, dico)
    element_modifie = BeautifulSoup(f"<{tag}>{texte_balisé}</{tag}>",'html.parser')
    texte.replaceWith(element_modifie)
    #if ident > 2:
      #break
    print("\n\n")
  pretty = soup.prettify()
  pretty = reprettify(pretty)
  open(fichier_sortie_xml,"w",encoding="utf8").write(pretty)
    

  


In [ ]:
def balise_texte(predictions, dico):
  
  texte_balisé = ""
  for preds, brut in zip(*predictions):
    print()
    for i in range(len(preds)):
      pred = preds[i]
      k, v  = [kv for kv in pred.items()][0]
      #print(k,"\t:\t",v)
      if v == "O":
        texte_balisé += k
      elif v.startswith("B-"):
        texte_balisé += "<"+ dico.get(v.strip('B-'))+">"+k
        try:
          k2, v2  = [kv2 for kv2 in preds[i+1].items()][0]
          if not v2.startswith("I-"):
            texte_balisé+= "</"+ dico.get(v.strip('B-'))+">"
        except IndexError:
          texte_balisé+= "</"+ dico.get(v.strip('B-'))+">"
      else:
        try:
          k2, v2  = [kv2 for kv2 in preds[i+1].items()][0]
          if v2.startswith("I-"):
            texte_balisé += k
          else:
            texte_balisé += k+"</"+ dico.get(v.strip('I-'))+">"
        except IndexError:
          texte_balisé += k+"</"+ dico.get(v.strip('I-'))+">"
      texte_balisé+=" "
    texte_balisé +="\n"
    #print(texte_balisé)
  return texte_balisé



In [ ]:
Etiquettage_Camembert(chemin+"/Corpus/Presse/grandfinal.xml",chemin+"/Corpus/Presse/grandfinal_annoté_camembert.xml", model)

1


  0%|          | 0/22 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/3 [00:00<?, ?it/s]


























2


  0%|          | 0/103 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]





353


  0%|          | 0/1 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]